In [1]:
import json
import ast
import csv
import ast
import pickle
import string
import requests
from Bio import SeqIO
from time import sleep
from concurrent.futures import ThreadPoolExecutor
from collections import defaultdict
import pandas as pd
import os
import functools
import operator as op
import numpy as np
from scipy.stats import binom
import nferx_py.fn as nf

product = lambda iterable: functools.reduce(op.mul, iterable, 1)
nf.authenticate("nikhilkayal@nference.net", "063a1c676867563c7898102c1dfd9b0e", "preview")

nferx_py v1.7.6 is currently installed. Please upgrade to the latest version v2.0.0. Installation link: https://github.com/lumenbiomics/nferx_py


2020-06-08 07:33:49,703 : INFO : URL: https://preview.nferx.com/api/is_authenticated, process-time: 0.4557149410247803
2020-06-08 07:33:49,704 : INFO : Authentication successful - nferX is online
2020-06-08 07:33:50,137 : INFO : URL: https://preview.nferx.com/api/get_data_versions, process-time: 0.4326448440551758
2020-06-08 07:33:50,138 : INFO : Data version "202003" has been set as default one


In [2]:
coronavirus = "/Users/nikhil/Downloads/601004676210-Coronaviridae_ProteinFastaResults.fasta"
human = "/Users/nikhil/nference/repositories/nfer/nferxapps/bio2vec_api/common/resources/uniprot-proteome-tabs.txt"

In [3]:
def parse_coronavirus_fasta(file):
    print("Reading: ", file)
    corona_family = {}
    for record in SeqIO.parse(file, "fasta"):
        corona_family[str(record.description)] = str(record.seq)
    corona_id_to_seq = {}
    corona_id_to_organism = {}
    corona_id_to_protein = {}
    for key, value in corona_family.items():
        corona_id = key.split("|")[1].split(":")[1]
        corona_organism = key.split("|")[3].split(":")[1]
        corona_id_to_seq[corona_id] = value
        corona_id_to_organism[corona_id] = corona_organism
        if len(key.split("|")) > 5:
            corona_protein = key.split("|")[5].split(":")[1]
        corona_id_to_protein[corona_id] = corona_protein
    organism_to_keys = defaultdict(list)
    for key, value in sorted(corona_id_to_organism.items()):
        organism_to_keys[value].append(key)
    organism_to_keys = dict(organism_to_keys)
    return corona_id_to_seq, corona_id_to_protein, organism_to_keys

In [4]:
corona_id_to_seq, corona_id_to_protein, organism_to_keys = parse_coronavirus_fasta(coronavirus)

Reading:  /Users/nikhil/Downloads/601004676210-Coronaviridae_ProteinFastaResults.fasta


In [6]:
organism_to_keys

{'Bovine coronavirus': ['AAA42912.1',
  'AAA42913.1',
  'AAA42914.1',
  'AAA66397.1',
  'AAK29738.2',
  'AAK29779.2',
  'AAK83354.1',
  'AAK83355.1',
  'AAK83356.1',
  'AAK83357.1',
  'AAK83358.1',
  'AAK83359.1',
  'AAK83360.1',
  'AAK83361.1',
  'AAK83362.1',
  'AAK83363.1',
  'AAL40398.1',
  'AAL40399.1',
  'AAL40400.1',
  'AAL40401.1',
  'AAL40402.1',
  'AAL40403.1',
  'AAL40404.1',
  'AAL40405.1',
  'AAL40406.1',
  'AAL40407.1',
  'AAL57306.1',
  'AAL57307.1',
  'AAL57308.1',
  'AAL57309.1',
  'AAL57310.1',
  'AAL57311.1',
  'AAL57312.1',
  'AAL57313.1',
  'AAL57314.1',
  'AAL57316.1',
  'AAP20417.1',
  'ANJ04972.1',
  'ANJ04973.1',
  'ANJ04974.1',
  'ANJ04975.1',
  'ANJ04976.1',
  'ANJ04977.1',
  'ANJ04978.1',
  'ANJ04979.1',
  'ANJ04980.1',
  'ARD05997.1',
  'ARD05998.1',
  'ARD05999.1',
  'ARD06000.1',
  'ARD06001.1',
  'ARD06002.1',
  'ARD06003.1',
  'ARD06004.1',
  'ARD06005.1',
  'ARD06007.1',
  'AVI14997.1',
  'AVI14998.1',
  'AVI14999.1',
  'AVI15000.1',
  'AVI15001.1',
  

In [5]:
def read_uniprot_exome(uniprot_exome_file):
    fd = open(uniprot_exome_file, 'rU')
    # delim = '\t' if (uniprot_exome_file.endswith('.tsv')) else ','
    delim = '\t'
    csv_file = csv.reader(fd, delimiter=delim)
    next(csv_file)  # skip header

    print("Reading: ", uniprot_exome_file)

    seq_dict = dict()
    protein_dict = dict()
    uniprot_dict = dict()
    uniprot2protein = dict()
    uniprot2gene = dict()

    for row in csv_file:
        uniprot_id = row[0]
        protein = row[1]
        gene = row[2]
        seq = row[3]

        if len(gene) == 0:
            if len(protein) > 0:
                gene = protein
            else:
                gene = ['uniprot_' + uniprot_id]
                pass
        gene_str = gene.split()[0]
        gene_str = gene_str.upper()
        seq_dict[gene_str] = seq
        protein_dict[gene_str] = protein
        uniprot_dict[uniprot_id] = seq
        uniprot2protein[uniprot_id] = protein
        uniprot2gene[uniprot_id] = gene_str

    return seq_dict, protein_dict, uniprot_dict, uniprot2protein, uniprot2gene

In [6]:
seq_dict, protein_dict, uniprot_dict, uniprot2protein, uniprot2gene = read_uniprot_exome(human)

Reading:  /Users/nikhil/nference/repositories/nfer/nferxapps/bio2vec_api/common/resources/uniprot-proteome-tabs.txt


In [7]:
# def count_nmers(sequence_dict, n):
#     counts = defaultdict(int)
#     for sequence in sequence_dict.values():
#         for start_ix in range(len(sequence) - n + 1):
#             counts[sequence[start_ix:start_ix + n]] += 1
#     series = pd.Series(counts)
#     return series

In [8]:
# def compute_probs(sequence_dict, n):
#     symbol_counts = count_nmers(sequence_dict, 1)
#     symbol_freqs = (symbol_counts / symbol_counts.sum()).to_dict()
#     counts = count_nmers(sequence_dict, n)
#     probs = {nmer: product(symbol_freqs[symbol] for symbol in nmer) for nmer in list(counts.index)}
#     series = pd.Series(probs)
#     return series

In [9]:
# def computer_nmer_suprise(sequence_dict, n, db):
# #     counts = self.count_nmers(n)
#     counts = pd.read_csv(db + "_{0}.csv".format(n), index_col=0, header=None, keep_default_na=False)[1]
# #     probs = self.compute_probs(n)
#     probs = pd.read_csv(db + "_prob_{0}.csv".format(n), index_col=0, header=None, keep_default_na=False)[1]
#     total_length_n_sequences = sum(max(0, len(seq) - n + 1) for seq in sequence_dict.values())
#     expected = probs * total_length_n_sequences
#     surprise_ratios = counts / expected
#     log2_surprise_ratio = np.log2(surprise_ratios)
#     variances = probs * (1 - probs) * total_length_n_sequences
#     stds = np.sqrt(variances)
#     stds_from_mean = (counts - expected) / stds
#     percentiles = np.array([binom.cdf(count, n=total_length_n_sequences, p=prob)
#                                     for count, prob in zip(counts, probs)])
#     survivals = np.array([binom.sf(count, n=total_length_n_sequences, p=prob)
#                                   for count, prob in zip(counts, probs)])  # 1 - percentiles, but more accurate
#     uniqueness_percentile_score = -np.log10(percentiles * 100)
#     uniqueness_percentile_score[np.isinf(uniqueness_percentile_score)] = 500
#     conservation_percentile_score = -np.log10(survivals * 100)
#     conservation_percentile_score[np.isinf(conservation_percentile_score)] = 500
#     df = pd.DataFrame(dict(
#                     count=counts,
#                     probability=probs,
#                     expected=expected,
#                     surprise_ratio=surprise_ratios,
#                     log2_surprise_ratio=log2_surprise_ratio,
#                     std=stds,
#                     stds_from_mean=stds_from_mean,
#                     percentile=percentiles,
#                     uniqueness_percentile_score=uniqueness_percentile_score,
#                     conservation_percentile_score=conservation_percentile_score
#                 ))
#     return df

In [10]:
# uniprot_8_surprise = computer_nmer_suprise(uniprot_dict, 8, "uniprot")
# uniprot_8_surprise.to_csv("uniprot_8_surprise.csv")

# uniprot_9_surprise = computer_nmer_suprise(uniprot_dict, 9, "uniprot")
# uniprot_9_surprise.to_csv("uniprot_9_surprise.csv")

# uniprot_10_surprise = computer_nmer_suprise(uniprot_dict, 10, "uniprot")
# uniprot_10_surprise.to_csv("uniprot_10_surprise.csv")

# viral_8_surprise = computer_nmer_suprise(corona_id_to_seq, 8, "viral")
# viral_8_surprise.to_csv("coronavirus/corona_8_surprise.csv")

# viral_9_surprise = computer_nmer_suprise(corona_id_to_seq, 9, "viral")
# viral_9_surprise.to_csv("coronavirus/corona_9_surprise.csv")

# viral_10_surprise = computer_nmer_suprise(corona_id_to_seq, 10, "viral")
# viral_10_surprise.to_csv("coronavirus/corona_10_surprise.csv")

In [11]:
def nmer_intersection(n, viral_sequence_dict=corona_id_to_seq, human_sequence_dict=uniprot_dict):
    if os.path.exists(os.path.join("/Users/nikhil/nference/problems/bat analysis/coronavirus/", '%smers.txt' % n)):
        with open("coronavirus/{0}mers.txt".format(n), "rb") as fp:
            intersection = pickle.load(fp)
    else: 
        viral_counts = defaultdict(int)
        for sequence in viral_sequence_dict.values():
            for start_ix in range(len(sequence) - n + 1):
                viral_counts[sequence[start_ix:start_ix + n]] += 1
        viral_series = pd.Series(viral_counts)
        viral_nmer_list = pd.DataFrame(viral_series).reset_index(level=0).rename(columns={"index":"nmer"})["nmer"].to_list()
        human_counts = defaultdict(int)
        for sequence in human_sequence_dict.values():
            for start_ix in range(len(sequence) - n + 1):
                human_counts[sequence[start_ix:start_ix + n]] += 1
        human_series = pd.Series(human_counts)
        human_nmer_list = pd.DataFrame(human_series).reset_index(level=0).rename(columns={"index":"nmer"})["nmer"].to_list()

        intersection = list(set(viral_nmer_list) & set(human_nmer_list))
        with open("coronavirus/{0}mers.txt".format(n), "wb") as fp:
            pickle.dump(intersection, fp)
    return intersection

In [12]:
iter_8 = nmer_intersection(8)
iter_9 = nmer_intersection(9)
iter_10 = nmer_intersection(10)
iter_11 = nmer_intersection(11)
iter_12 = nmer_intersection(12)

In [13]:
def make_pairs(intersection_nmer_list):
    length = len(intersection_nmer_list[0])
    if os.path.exists(os.path.join("/Users/nikhil/nference/problems/bat analysis/coronavirus/", '%smers.json' % length)):
        with open("coronavirus/{0}mers.json".format(length), "rb") as fp:
            iter_dict = json.load(fp)
    else:
        iter_dict = {}
        for nmer in intersection_nmer_list:
            corresponding_list = []
            for uniprot_id, uniprot_sequence in uniprot_dict.items():
                if nmer in uniprot_sequence:
                    corresponding_dict = {}
                    corresponding_dict[uniprot_id] = uniprot2gene[uniprot_id]
                    corresponding_list.append(corresponding_dict)
            for viral_id, viral_sequence in corona_id_to_seq.items():
                if nmer in viral_sequence:
                    corresponding_dict = {}
                    corresponding_dict[viral_id] = corona_id_to_protein[viral_id]
                    corresponding_list.append(corresponding_dict)
            iter_dict[nmer] = corresponding_list
        with open('coronavirus/{0}mers.json'.format(length), 'w') as file:
            json.dump(iter_dict, file, indent=2)
    return iter_dict

In [14]:
pair_8 = make_pairs(iter_8)
pair_9 = make_pairs(iter_9)
pair_10 = make_pairs(iter_10)
pair_11 = make_pairs(iter_11)
pair_12 = make_pairs(iter_12)

In [15]:
new_organism_to_keys = dict()
for key, value in organism_to_keys.items():
    key = key.replace("/", " ").translate(str.maketrans('', '', string.punctuation)).replace(" ", "_").lower()
    new_organism_to_keys[key] = value

In [16]:
new_organism_to_keys.keys()

dict_keys(['bovine_coronavirus', 'infectious_bronchitis_virus', 'murine_hepatitis_virus', 'murine_hepatitis_virus_strain_2', 'murine_hepatitis_virus_strain_ml11', 'human_coronavirus_229e', 'porcine_epidemic_diarrhea_virus', 'sars_coronavirus_urbani', 'sars_coronavirus_cuhkw1', 'sars_coronavirus_bj01', 'sars_coronavirus_cuhksu10', 'sars_coronavirus_frankfurt_1', 'sars_coronavirus_tw1', 'sars_coronavirus_tor2', 'sars_coronavirus_fra', 'sars_coronavirus_gd01', 'sars_coronavirus_hsr_1', 'sars_coronavirus_shanghaiqxc1', 'sars_coronavirus_cuhkag01', 'sars_coronavirus_cuhkag02', 'sars_coronavirus_cuhkag03', 'sars_coronavirus_taiwan_tc3', 'sars_coronavirus_taiwan_tc1', 'sars_coronavirus_taiwan_tc2', 'sars_coronavirus_as', 'human_coronavirus_oc43', 'sars_coronavirus_pumc01', 'sars_coronavirus_pumc02', 'sars_coronavirus_pumc03', 'sars_coronavirus_sino111', 'sars_coronavirus_sino311', 'sars_coronavirus_shanghaiqxc2', 'sars_coronavirus_tw10', 'sars_coronavirus_tw11', 'sars_coronavirus_tw2', 'sars_

In [17]:
new_organism_to_keys["common_moorhen_coronavirus_hku21"]

['YP_005352881.1',
 'YP_005352882.1',
 'YP_005352883.1',
 'YP_005352884.1',
 'YP_005352885.1',
 'YP_005352886.1',
 'YP_005352887.1',
 'YP_005352888.1']

In [18]:
organisms_to_nmers = dict()
for key, value in new_organism_to_keys.items():
    print(key)
    organism_list = []
    eight_mers = []
    nine_mers = []
    ten_mers = []
    eleven_mers = []
    tweleve_mers = []
    for corona_id in value:
        for nmer, pairs in pair_8.items():
            for item in pairs:
                if corona_id in list(item.keys()):
                    temp_dict = {}
                    temp_dict[nmer] = pairs
                    eight_mers.append(temp_dict)
        for nmer, pairs in pair_9.items():
            for item in pairs:
                if corona_id in list(item.keys()):
                    temp_dict = {}
                    temp_dict[nmer] = pairs
                    nine_mers.append(temp_dict)
        for nmer, pairs in pair_10.items():
            for item in pairs:
                if corona_id in list(item.keys()):
                    temp_dict = {}
                    temp_dict[nmer] = pairs
                    ten_mers.append(temp_dict)
        for nmer, pairs in pair_11.items():
            for item in pairs:
                if corona_id in list(item.keys()):
                    temp_dict = {}
                    temp_dict[nmer] = pairs
                    eleven_mers.append(temp_dict)
        for nmer, pairs in pair_12.items():
            for item in pairs:
                if corona_id in list(item.keys()):
                    temp_dict = {}
                    temp_dict[nmer] = pairs
                    tweleve_mers.append(temp_dict)
                        
    organism_list.extend(eight_mers + nine_mers + ten_mers + eleven_mers + tweleve_mers)
#     master_list = []
#     for item in organism_list:
#         for key_, value_ in item.items():
#             for pair in value_:
#                 another_dict = dict()
#                 another_dict["peptide"] = key_
#                 another_dict["peptide_length"] = len(key_)
#                 for key1, value in pair.items():
#                     if "." in key1:
#                         another_dict["viral_surprise_score"] = None
#                         another_dict["viral_protein"] = value
#                         another_dict["viral_protein_annotation"] = key1
#                         another_dict["viral_protein_peptide_start"] = corona_id_to_seq[another_dict["viral_protein_annotation"]].find(another_dict["peptide"])
#                         another_dict["viral_protein_peptide_end"] = another_dict["viral_protein_peptide_start"] + len(another_dict["peptide"]) - 1

#                     else:
#                         another_dict["human_surprise_score"] = None
#                         another_dict["human_protein"] = value
#                         another_dict["human_protein_annotation"] = key1
#                         another_dict["human_protein_peptide_start"] = uniprot_dict[another_dict["human_protein_annotation"]].find(another_dict["peptide"])
#                         another_dict["human_protein_peptide_end"] = another_dict["human_protein_peptide_start"] + len(another_dict["peptide"]) - 1
#                 master_list.append(another_dict)
    organisms_to_nmers[key] = organism_list

bovine_coronavirus
infectious_bronchitis_virus


KeyboardInterrupt: 

In [ ]:
with open("coronavirus/intermediate_dump.json", "r") as fp:
    organisms_to_nmers = json.load(fp)

In [ ]:
import pickle
with open('coronavirus/intermediate_dump.pickle', 'wb') as handle:
    pickle.dump(organisms_to_nmers, handle)

In [22]:
organisms_to_nmers

{'bovine_coronavirus': [{'peptide': 'RASSRASS',
   'peptide_length': 8,
   'human_surprise_score': None,
   'human_protein': 'GJA1',
   'human_protein_annotation': 'P17302',
   'human_protein_peptide_start': 365,
   'human_protein_peptide_end': 372},
  {'peptide': 'RASSRASS',
   'peptide_length': 8,
   'viral_surprise_score': None,
   'viral_protein': 'nucleocapsid protein',
   'viral_protein_annotation': 'AYR18612.1',
   'viral_protein_peptide_start': 198,
   'viral_protein_peptide_end': 205},
  {'peptide': 'RASSRASS',
   'peptide_length': 8,
   'viral_surprise_score': None,
   'viral_protein': 'nucleocapsid protein',
   'viral_protein_annotation': 'AYR18630.1',
   'viral_protein_peptide_start': 198,
   'viral_protein_peptide_end': 205},
  {'peptide': 'RASSRASS',
   'peptide_length': 8,
   'viral_surprise_score': None,
   'viral_protein': 'nucleocapsid protein',
   'viral_protein_annotation': 'AYR18639.1',
   'viral_protein_peptide_start': 198,
   'viral_protein_peptide_end': 205},
  

In [24]:
def explode(df, lst_cols, fill_value=''):
    # make sure `lst_cols` is a list
    if lst_cols and not isinstance(lst_cols, list):
        lst_cols = [lst_cols]
    # all columns except `lst_cols`
    idx_cols = df.columns.difference(lst_cols)

    # calculate lengths of lists
    lens = df[lst_cols[0]].str.len()

    if (lens > 0).all():
        # ALL lists in cells aren't empty
        return pd.DataFrame({
            col:np.repeat(df[col].values, df[lst_cols[0]].str.len())
            for col in idx_cols
        }).assign(**{col:np.concatenate(df[col].values) for col in lst_cols}) \
          .loc[:, df.columns]
    else:
        # at least one list in cells is empty
        return pd.DataFrame({
            col:np.repeat(df[col].values, df[lst_cols[0]].str.len())
            for col in idx_cols
        }).assign(**{col:np.concatenate(df[col].values) for col in lst_cols}) \
          .append(df.loc[lens==0, idx_cols]).fillna(fill_value) \
          .loc[:, df.columns]

In [27]:
def unstack_df(df):
    x = explode(df, lst_cols=["human_protein_annotation", "human_protein"])
    x = explode(x, lst_cols=["viral_protein_annotation", "viral_protein"])
    return x

In [28]:
unstack_df(t)

ValueError: count < 0

In [55]:
# Don't need anymore 3:28 pm

# all_interested_keys = []
# for key, value in uniprot2gene.items():
#     all_interested_keys.append(key)
# for key, value in interested_viral.items():
#     all_interested_keys.append(key)

In [56]:
# Don't need anymore 3:28 pm

# def keep_corona(dict_pair):
#     for nmer, pairs in dict_pair.items():
#         pairs = [{k: v for k, v in d.items() if k in all_interested_keys} for d in pairs]
#         pairs = list(filter(None, pairs))
#         dict_pair[nmer] = pairs
#     return dict_pair

In [57]:
# Don't need anymore 3:28 pm

# pair_8 = keep_corona(pair_8)
# pair_9 = keep_corona(pair_9)
# pair_10 = keep_corona(pair_10)

In [58]:
# have all the species keys in organism_to_keys dictionary don't need 3:41

# sars = {}
# mers = {}
# sars_2 = {}
# # human_corona = {}
# hcov_229E = {}
# hcov_OC43 = {}
# hcov_HKU1 = {}
# hcov_NL63 = {}


# rousettus_bat = {} ########################
# rousettus_bat_HKU9 = {}
# rousettus_bat_HKU10 = {}
# bat_BM48 = {}
# bat_CDPHE15 = {}
# bat_1A = {}
# tylonycteris_HKU4 = {}
# scotophilus_512 = {}
# pipistrellus_HKU5 = {}
# bat_NL63 = {}
# bat_hp = {}
# rhinolophus_HKU2 = {}
# miniopterus_HKU8 = {}
# bat_coronavirus = {}  ###################################

# munia = {}
# bovine = {}
# rabbit = {}
# turkey = {}
# porcine_epidemic = {}
# wencheng = {}
# betacoronavirus_erinaceus = {}
# porcine_HKU15 = {}
# rat = {}
# white_eye = {}
# thrush = {}
# beluga = {}
# camel = {}
# wigeon = {}
# lucheng = {}
# sparrow = {}
# bulbul = {}
# swine = {}
# magpie = {}
# mink = {}
# bronchitis = {}
# moorhen = {}
# betacoronavirus_HKU24 = {}
# ferret = {}
# betacoronavirus_england = {}
# heron = {}


# for key, value in interested_viral.items():
#     if "Severe acute respiratory syndrome coronavirus 2" in value:
#         sars_2[key] = value
#     elif "Severe acute respiratory syndrome-related coronavirus" in value:
#         sars[key] = value
#     elif "Middle East respiratory syndrome-related coronavirus" in value:
#         mers[key] = value
#     elif "Bat coronavirus CDPHE15/USA/2006" in value:
#         bat_CDPHE15[key] = value
#     elif "Tylonycteris bat coronavirus HKU4" in value:
#         tylonycteris_HKU4[key] = value
#     elif "Bat coronavirus 1A" in value:
#         bat_1A[key] = value
#     elif "Scotophilus bat coronavirus 512" in value:
#         scotophilus_512[key] = value
#     elif "Pipistrellus bat coronavirus HKU5" in value:
#         pipistrellus_HKU5[key] = value
#     elif "NL63-related bat coronavirus" in value:
#         bat_NL63[key] = value
#     elif "Miniopterus bat coronavirus HKU8" in value:
#         miniopterus_HKU8[key] = value
#     elif "Bat Hp-betacoronavirus/Zhejiang2013" in value:
#         bat_hp[key] = value
#     elif "Rhinolophus bat coronavirus HKU2" in value:
#         rhinolophus_HKU2[key] = value
#     elif "Rousettus bat coronavirus HKU9" in value:
#         rousettus_bat_HKU9[key] = value
#     elif "Rousettus bat coronavirus HKU10" in value:
#         rousettus_bat_HKU10[key] = value
#     elif "Bat coronavirus BM48-31/BGR/2008" in value:
#         bat_BM48[key] = value
#     elif "Human coronavirus 229E" in value:
#         hcov_229E[key] = value
#     elif "Human coronavirus NL63" in value:
#         hcov_NL63[key] = value
#     elif "Human coronavirus HKU1" in value:
#         hcov_HKU1[key] = value
#     elif "Human coronavirus OC43" in value:
#         hcov_OC43[key] = value
#     elif "Munia coronavirus HKU13-3514" in value:
#         munia[key] = value
#     elif "Bovine coronavirus" in value:
#         bovine[key] = value
#     elif "Rabbit coronavirus HKU14" in value:
#         rabbit[key] = value
#     elif "Turkey coronavirus" in value:
#         turkey[key] = value
#     elif "Porcine epidemic diarrhea virus" in value:
#         porcine_epidemic[key] = value
#     elif "Wencheng Sm shrew coronavirus" in value:
#         wencheng[key] = value
#     elif "Betacoronavirus Erinaceus/VMC/DEU/2012" in value:
#         betacoronavirus_erinaceus[key] = value
#     elif "Porcine coronavirus HKU15" in value:
#         porcine_HKU15[key] = value
#     elif "Rat coronavirus Parker" in value:
#         rat[key] = value
#     elif "White-eye coronavirus HKU16" in value:
#         white_eye[key] = value
#     elif "Thrush coronavirus HKU12-600" in value:
#         thrush[key] = value
#     elif "Beluga whale coronavirus SW1" in value:
#         beluga[key] = value
#     elif "Camel alphacoronavirus" in value:
#         camel[key] = value
#     elif "Wigeon coronavirus HKU20" in value:
#         wigeon[key] = value
#     elif "Lucheng Rn rat coronavirus" in value:
#         lucheng[key] = value
#     elif "Sparrow coronavirus HKU17" in value:
#         sparrow[key] = value
#     elif "Bulbul coronavirus HKU11-934" in value:
#         bulbul[key] = value
#     elif "Swine enteric coronavirus" in value:
#         swine[key] = value
#     elif "Magpie-robin coronavirus HKU18" in value:
#         magpie[key] = value
#     elif "Mink coronavirus strain WD1127" in value:
#         mink[key] = value
#     elif "Infectious bronchitis virus" in value:
#         bronchitis[key] = value
#     elif "Common moorhen coronavirus HKU21" in value:
#         moorhen[key] = value
#     elif "Betacoronavirus HKU24" in value:
#         betacoronavirus_HKU24[key] = value
#     elif "Ferret coronavirus" in value:
#         ferret[key] = value
#     elif "Betacoronavirus England 1" in value:
#         betacoronavirus_england[key] = value
#     elif "Night heron coronavirus HKU19" in value:
#         heron[key] = value

In [62]:
# have all the species keys in organism_to_keys dictionary don't need 3:41

# keys_to_remove_rousettus_bat = []
# all_rousettus_bat_keys = []
# for key in rousettus_bat_HKU10.keys():
#     keys_to_remove_rousettus_bat.append(key)
# for key in rousettus_bat_HKU9.keys():
#     keys_to_remove_rousettus_bat.append(key)
# for key, value in interested_viral.items():
#     if "Rousettus bat coronavirus" in value:
#         all_rousettus_bat_keys.append(key)
# needed_keys_rousettus_bat = list(set(all_rousettus_bat_keys) - set(keys_to_remove_rousettus_bat))

# keys_to_remove_bat = []
# all_normal_bat_keys = []
# for key in bat_BM48.keys():
#     keys_to_remove_bat.append(key)
# for key in bat_CDPHE15.keys():
#     keys_to_remove_bat.append(key)
# for key in bat_1A.keys():
#     keys_to_remove_bat.append(key)
# for key, value in interested_viral.items():
#     if "Bat coronavirus" in value:
#         all_normal_bat_keys.append(key)
# needed_keys_bat = list(set(all_normal_bat_keys) - set(keys_to_remove_bat))

In [63]:
# have all the species keys in organism_to_keys dictionary don't need 3:41

# for key, value in interested_viral.items():
#     if key in needed_keys_rousettus_bat:
#         rousettus_bat[key] = value
#     elif key in needed_keys_bat:
#         bat_coronavirus[key] = value

In [64]:
def interested_keys(dict_item):
    l = []
    for key, value in uniprot2gene.items():
        l.append(key)
    for key, value in dict_item.items():
        l.append(key)
    return l

In [66]:
all_interested_keys_sars_2 = interested_keys(sars_2)
all_interested_keys_sars = interested_keys(sars)
all_interested_keys_mers = interested_keys(mers)
all_interested_keys_hcov_229E = interested_keys(hcov_229E)
all_interested_keys_hcov_NL63 = interested_keys(hcov_NL63)
all_interested_keys_hcov_HKU1 = interested_keys(hcov_HKU1)
all_interested_keys_hcov_OC43 = interested_keys(hcov_OC43)
all_interested_keys_rousettus_bat = interested_keys(rousettus_bat)
all_interested_keys_rousettus_bat_HKU9 = interested_keys(rousettus_bat_HKU9)
all_interested_keys_rousettus_bat_HKU10 = interested_keys(rousettus_bat_HKU10)
all_interested_keys_bat_BM48 = interested_keys(bat_BM48)
all_interested_keys_bat_CDPHE15 = interested_keys(bat_CDPHE15)
all_interested_keys_bat_1A = interested_keys(bat_1A)
all_interested_keys_tylonycteris_HKU4 = interested_keys(tylonycteris_HKU4)
all_interested_keys_scotophilus_512 = interested_keys(scotophilus_512)
all_interested_keys_pipistrellus_HKU5 = interested_keys(pipistrellus_HKU5)
all_interested_keys_bat_NL63 = interested_keys(bat_NL63)
all_interested_keys_bat_hp = interested_keys(bat_hp)
all_interested_keys_rhinolophus_HKU2 = interested_keys(rhinolophus_HKU2)
all_interested_keys_miniopterus_HKU8 = interested_keys(miniopterus_HKU8)
all_interested_keys_bat_coronavirus = interested_keys(bat_coronavirus)
all_interested_keys_munia = interested_keys(munia)
all_interested_keys_bovine = interested_keys(bovine)
all_interested_keys_rabbit = interested_keys(rabbit)
all_interested_keys_turkey = interested_keys(turkey)
all_interested_keys_porcine_epidemic = interested_keys(porcine_epidemic)
all_interested_keys_wencheng = interested_keys(wencheng)
all_interested_keys_betacoronavirus_erinaceus = interested_keys(betacoronavirus_erinaceus)
all_interested_keys_porcine_HKU15 = interested_keys(porcine_HKU15)
all_interested_keys_rat = interested_keys(rat)
all_interested_keys_white_eye = interested_keys(white_eye)
all_interested_keys_thrush = interested_keys(thrush)
all_interested_keys_beluga = interested_keys(beluga)
all_interested_keys_camel = interested_keys(camel)
all_interested_keys_wigeon = interested_keys(wigeon)
all_interested_keys_lucheng = interested_keys(lucheng)
all_interested_keys_sparrow = interested_keys(sparrow)
all_interested_keys_bulbul = interested_keys(bulbul)
all_interested_keys_swine = interested_keys(swine)
all_interested_keys_magpie = interested_keys(magpie)
all_interested_keys_mink = interested_keys(mink)
all_interested_keys_bronchitis = interested_keys(bronchitis)
all_interested_keys_moorhen = interested_keys(moorhen)
all_interested_keys_betacoronavirus_HKU24 = interested_keys(betacoronavirus_HKU24)
all_interested_keys_ferret = interested_keys(ferret)
all_interested_keys_betacoronavirus_england = interested_keys(betacoronavirus_england)
all_interested_keys_heron = interested_keys(heron)

In [69]:
def keep_type(dict_pair, interested_keys):
    for nmer, pairs in dict_pair.items():
        pairs = [{k: v for k, v in d.items() if k in interested_keys} for d in pairs]
        pairs = list(filter(None, pairs))
        dict_pair[nmer] = pairs
    return dict_pair

In [70]:
def dump_json(species, n, dict_item):
    with open('{0}_pair_{1}.json'.format(species, n), 'w') as fp:
        json.dump(dict_item, fp)

In [80]:
# sars_2_pair_8 = keep_type(corona_8mers, all_interested_keys_sars_2)
# sars_2_pair_9 = keep_type(corona_9mers, all_interested_keys_sars_2)
# sars_2_pair_10 = keep_type(corona_10mers, all_interested_keys_sars_2)
# sars_pair_8 = keep_type(corona_8mers, all_interested_keys_sars)
# sars_pair_9 = keep_type(corona_9mers, all_interested_keys_sars)
# sars_pair_10 = keep_type(corona_10mers, all_interested_keys_sars)
# mers_pair_8 = keep_type(corona_8mers, all_interested_keys_mers)
# mers_pair_9 = keep_type(corona_9mers, all_interested_keys_mers)
# mers_pair_10 = keep_type(corona_10mers, all_interested_keys_mers)

# hcov_OC43_pair_8 = keep_type(corona_8mers, all_interested_keys_hcov_OC43)
# hcov_OC43_pair_9 = keep_type(corona_9mers, all_interested_keys_hcov_OC43)
# hcov_OC43_pair_10 = keep_type(corona_10mers, all_interested_keys_hcov_OC43)

# rousettus_bat_pair_8 = keep_type(corona_8mers, all_interested_keys_rousettus_bat)
# rousettus_bat_pair_9 = keep_type(corona_9mers, all_interested_keys_rousettus_bat)
# rousettus_bat_pair_10 = keep_type(corona_10mers, all_interested_keys_rousettus_bat)
# rousettus_bat_HKU10_pair_8 = keep_type(corona_8mers, all_interested_keys_rousettus_bat_HKU10)
# rousettus_bat_HKU10_pair_9 = keep_type(corona_9mers, all_interested_keys_rousettus_bat_HKU10)
# rousettus_bat_HKU10_pair_10 = keep_type(corona_10mers, all_interested_keys_rousettus_bat_HKU10)
# lucheng_pair_8 = keep_type(corona_8mers, all_interested_keys_lucheng)
# lucheng_pair_9 = keep_type(corona_9mers, all_interested_keys_lucheng)
# lucheng_pair_10 = keep_type(corona_10mers, all_interested_keys_lucheng)


In [81]:
# dump_json("hcov_OC43", 8, hcov_OC43_pair_8)
# dump_json("hcov_OC43", 9, hcov_OC43_pair_9)
# dump_json("hcov_OC43", 10, hcov_OC43_pair_10)

In [83]:
def read_json(species, n):
    with open('{0}_pair_{1}.json'.format(species, n), 'r') as fp:
        pair = json.load(fp)
    return pair

In [84]:
sars_2_pair_8 = read_json("sars_2", 8)
sars_2_pair_9 = read_json("sars_2", 9)
sars_2_pair_10 = read_json("sars_2", 10)

sars_pair_8 = read_json("sars", 8)
sars_pair_9 = read_json("sars", 9)
sars_pair_10 = read_json("sars", 10)

mers_pair_8 = read_json("mers", 8)
mers_pair_9 = read_json("mers", 9)
mers_pair_10 = read_json("mers", 10)

hcov_229E_pair_8 = read_json("hcov_229E", 8)
hcov_229E_pair_9 = read_json("hcov_229E", 9)
hcov_229E_pair_10 = read_json("hcov_229E", 10)

hcov_NL63_pair_8 = read_json("hcov_NL63", 8)
hcov_NL63_pair_9 = read_json("hcov_NL63", 9)
hcov_NL63_pair_10 = read_json("hcov_NL63", 10)

hcov_HKU1_pair_8 = read_json("hcov_HKU1", 8)
hcov_HKU1_pair_9 = read_json("hcov_HKU1", 9)
hcov_HKU1_pair_10 = read_json("hcov_HKU1", 10)

hcov_OC43_pair_8 = read_json("hcov_OC43", 8)
hcov_OC43_pair_9 = read_json("hcov_OC43", 9)
hcov_OC43_pair_10 = read_json("hcov_OC43", 10)

In [85]:
# Reading all Bats
rousettus_bat_pair_8 = read_json("rousettus_bat", 8)
rousettus_bat_pair_9 = read_json("rousettus_bat", 9)
rousettus_bat_pair_10 = read_json("rousettus_bat", 10)

rousettus_bat_HKU9_pair_8 = read_json("rousettus_bat_HKU9", 8)
rousettus_bat_HKU9_pair_9 = read_json("rousettus_bat_HKU9", 9)
rousettus_bat_HKU9_pair_10 = read_json("rousettus_bat_HKU9", 10)

rousettus_bat_HKU10_pair_8 = read_json("rousettus_bat_HKU10", 8)
rousettus_bat_HKU10_pair_9 = read_json("rousettus_bat_HKU10", 9)
rousettus_bat_HKU10_pair_10 = read_json("rousettus_bat_HKU10", 10)

bat_BM48_pair_8 = read_json("bat_BM48", 8)
bat_BM48_pair_9 = read_json("bat_BM48", 9)
bat_BM48_pair_10 = read_json("bat_BM48", 10)

bat_CDPHE15_pair_8 = read_json("bat_CDPHE15", 8)
bat_CDPHE15_pair_9 = read_json("bat_CDPHE15", 9)
bat_CDPHE15_pair_10 = read_json("bat_CDPHE15", 10)

bat_1A_pair_8 = read_json("bat_1A", 8)
bat_1A_pair_9 = read_json("bat_1A", 9)
bat_1A_pair_10 = read_json("bat_1A", 10)

tylonycteris_HKU4_pair_8 = read_json("tylonycteris_HKU4", 8)
tylonycteris_HKU4_pair_9 = read_json("tylonycteris_HKU4", 9)
tylonycteris_HKU4_pair_10 = read_json("tylonycteris_HKU4", 10)

scotophilus_512_pair_8 = read_json("scotophilus_512", 8)
scotophilus_512_pair_9 = read_json("scotophilus_512", 9)
scotophilus_512_pair_10 = read_json("scotophilus_512", 10)

pipistrellus_HKU5_pair_8 = read_json("pipistrellus_HKU5", 8)
pipistrellus_HKU5_pair_9 = read_json("pipistrellus_HKU5", 9)
pipistrellus_HKU5_pair_10 = read_json("pipistrellus_HKU5", 10)

bat_NL63_pair_8 = read_json("bat_NL63", 8)
bat_NL63_pair_9 = read_json("bat_NL63", 9)
bat_NL63_pair_10 = read_json("bat_NL63", 10)

bat_hp_pair_8 = read_json("bat_hp", 8)
bat_hp_pair_9 = read_json("bat_hp", 9)
bat_hp_pair_10 = read_json("bat_hp", 10)

rhinolophus_HKU2_pair_8 = read_json("rhinolophus_HKU2", 8)
rhinolophus_HKU2_pair_9 = read_json("rhinolophus_HKU2", 9)
rhinolophus_HKU2_pair_10 = read_json("rhinolophus_HKU2", 10)

miniopterus_HKU8_pair_8 = read_json("miniopterus_HKU8", 8)
miniopterus_HKU8_pair_9 = read_json("miniopterus_HKU8", 9)
miniopterus_HKU8_pair_10 = read_json("miniopterus_HKU8", 10)

bat_coronavirus_pair_8 = read_json("bat_coronavirus", 8)
bat_coronavirus_pair_9 = read_json("bat_coronavirus", 9)
bat_coronavirus_pair_10 = read_json("bat_coronavirus", 10)

In [86]:
# Reading other species
munia_pair_8 = read_json("munia", 8)
munia_pair_9 = read_json("munia", 9)
munia_pair_10 = read_json("munia", 10)

bovine_pair_8 = read_json("bovine", 8)
bovine_pair_9 = read_json("bovine", 9)
bovine_pair_10 = read_json("bovine", 10)

rabbit_pair_8 = read_json("rabbit", 8)
rabbit_pair_9 = read_json("rabbit", 9)
rabbit_pair_10 = read_json("rabbit", 10)

turkey_pair_8 = read_json("turkey", 8)
turkey_pair_9 = read_json("turkey", 9)
turkey_pair_10 = read_json("turkey", 10)

porcine_epidemic_pair_8 = read_json("porcine_epidemic", 8)
porcine_epidemic_pair_9 = read_json("porcine_epidemic", 9)
porcine_epidemic_pair_10 = read_json("porcine_epidemic", 10)

wencheng_pair_8 = read_json("wencheng", 8)
wencheng_pair_9 = read_json("wencheng", 9)
wencheng_pair_10 = read_json("wencheng", 10)

betacoronavirus_erinaceus_pair_8 = read_json("betacoronavirus_erinaceus", 8)
betacoronavirus_erinaceus_pair_9 = read_json("betacoronavirus_erinaceus", 9)
betacoronavirus_erinaceus_pair_10 = read_json("betacoronavirus_erinaceus", 10)

porcine_HKU15_pair_8 = read_json("porcine_HKU15", 8)
porcine_HKU15_pair_9 = read_json("porcine_HKU15", 9)
porcine_HKU15_pair_10 = read_json("porcine_HKU15", 10)

rat_pair_8 = read_json("rat", 8)
rat_pair_9 = read_json("rat", 9)
rat_pair_10 = read_json("rat", 10)

white_eye_pair_8 = read_json("white_eye", 8)
white_eye_pair_9 = read_json("white_eye", 9)
white_eye_pair_10 = read_json("white_eye", 10)

thrush_pair_8 = read_json("thrush", 8)
thrush_pair_9 = read_json("thrush", 9)
thrush_pair_10 = read_json("thrush", 10)

beluga_pair_8 = read_json("beluga", 8)
beluga_pair_9 = read_json("beluga", 9)
beluga_pair_10 = read_json("beluga", 10)

camel_pair_8 = read_json("camel", 8)
camel_pair_9 = read_json("camel", 9)
camel_pair_10 = read_json("camel", 10)

wigeon_pair_8 = read_json("wigeon", 8)
wigeon_pair_9 = read_json("wigeon", 9)
wigeon_pair_10 = read_json("wigeon", 10)

lucheng_pair_8 = read_json("lucheng", 8)
lucheng_pair_9 = read_json("lucheng", 9)
lucheng_pair_10 = read_json("lucheng", 10)

sparrow_pair_8 = read_json("sparrow", 8)
sparrow_pair_9 = read_json("sparrow", 9)
sparrow_pair_10 = read_json("sparrow", 10)

bulbul_pair_8 = read_json("bulbul", 8)
bulbul_pair_9 = read_json("bulbul", 9)
bulbul_pair_10 = read_json("bulbul", 10)

swine_pair_8 = read_json("swine", 8)
swine_pair_9 = read_json("swine", 9)
swine_pair_10 = read_json("swine", 10)

magpie_pair_8 = read_json("magpie", 8)
magpie_pair_9 = read_json("magpie", 9)
magpie_pair_10 = read_json("magpie", 10)

mink_pair_8 = read_json("mink", 8)
mink_pair_9 = read_json("mink", 9)
mink_pair_10 = read_json("mink", 10)

bronchitis_pair_8 = read_json("bronchitis", 8)
bronchitis_pair_9 = read_json("bronchitis", 9)
bronchitis_pair_10 = read_json("bronchitis", 10)

moorhen_pair_8 = read_json("moorhen", 8)
moorhen_pair_9 = read_json("moorhen", 9)
moorhen_pair_10 = read_json("moorhen", 10)

betacoronavirus_HKU24_pair_8 = read_json("betacoronavirus_HKU24", 8)
betacoronavirus_HKU24_pair_9 = read_json("betacoronavirus_HKU24", 9)
betacoronavirus_HKU24_pair_10 = read_json("betacoronavirus_HKU24", 10)

ferret_pair_8 = read_json("ferret", 8)
ferret_pair_9 = read_json("ferret", 9)
ferret_pair_10 = read_json("ferret", 10)

betacoronavirus_england_pair_8 = read_json("betacoronavirus_england", 8)
betacoronavirus_england_pair_9 = read_json("betacoronavirus_england", 9)
betacoronavirus_england_pair_10 = read_json("betacoronavirus_england", 10)

heron_pair_8 = read_json("heron", 8)
heron_pair_9 = read_json("heron", 9)
heron_pair_10 = read_json("heron", 10)

In [88]:
def convert_to_df(pair):
    t = []
    for nmer, pairs in  pair.items():
        uniprot_id = []
        viral_id = []
        uniprot_annotation = []
        viral_annotation = []
        temp_dict = {}
        temp_dict["nmer"] = nmer
        temp_dict["length"] = len(nmer)
        for pair in pairs:
            for key, value in pair.items():
                if "." in key:
                    viral_id.append(key)
                    viral_annotation.append(value)
                else:
                    uniprot_id.append(key)
                    uniprot_annotation.append(value)
        temp_dict["uniprot_annotation"] = uniprot_id
        temp_dict["uniprot_gene"] = uniprot_annotation
        temp_dict["viral_annotation"] = viral_id
        temp_dict["viral_gene"] = viral_annotation
        t.append(temp_dict)
    t = pd.DataFrame(t)
    t = t[t.astype(str)['viral_annotation'] != '[]']
    return t.reset_index(drop=True)

In [89]:
sars_2_pair_8 = convert_to_df(sars_2_pair_8)
sars_2_pair_9 = convert_to_df(sars_2_pair_9)
sars_2_pair_10 = convert_to_df(sars_2_pair_10)

sars_pair_8 = convert_to_df(sars_pair_8)
sars_pair_9 = convert_to_df(sars_pair_9)
sars_pair_10 = convert_to_df(sars_pair_10)

mers_pair_8 = convert_to_df(mers_pair_8)
mers_pair_9 = convert_to_df(mers_pair_9)
mers_pair_10 = convert_to_df(mers_pair_10)

hcov_229E_pair_8 = convert_to_df(hcov_229E_pair_8)
hcov_229E_pair_9 = convert_to_df(hcov_229E_pair_9)
hcov_229E_pair_10 = convert_to_df(hcov_229E_pair_10)

hcov_HKU1_pair_8 = convert_to_df(hcov_HKU1_pair_8)
hcov_HKU1_pair_9 = convert_to_df(hcov_HKU1_pair_9)
hcov_HKU1_pair_10 = convert_to_df(hcov_HKU1_pair_10)

hcov_NL63_pair_8 = convert_to_df(hcov_NL63_pair_8)
hcov_NL63_pair_9 = convert_to_df(hcov_NL63_pair_9)
hcov_NL63_pair_10 = convert_to_df(hcov_NL63_pair_10)

hcov_OC43_pair_8 = convert_to_df(hcov_OC43_pair_8)
hcov_OC43_pair_9 = convert_to_df(hcov_OC43_pair_9)
hcov_OC43_pair_10 = convert_to_df(hcov_OC43_pair_10)

rousettus_bat_pair_8 = convert_to_df(rousettus_bat_pair_8)
rousettus_bat_pair_9 = convert_to_df(rousettus_bat_pair_9)
rousettus_bat_pair_10 = convert_to_df(rousettus_bat_pair_10)

rousettus_bat_HKU9_pair_8 = convert_to_df(rousettus_bat_HKU9_pair_8)
rousettus_bat_HKU9_pair_9 = convert_to_df(rousettus_bat_HKU9_pair_9)
rousettus_bat_HKU9_pair_10 = convert_to_df(rousettus_bat_HKU9_pair_10)

rousettus_bat_HKU10_pair_8 = convert_to_df(rousettus_bat_HKU10_pair_8)
rousettus_bat_HKU10_pair_9 = convert_to_df(rousettus_bat_HKU10_pair_9)
rousettus_bat_HKU10_pair_10 = convert_to_df(rousettus_bat_HKU10_pair_10)

bat_BM48_pair_8 = convert_to_df(bat_BM48_pair_8)
bat_BM48_pair_9 = convert_to_df(bat_BM48_pair_9)
bat_BM48_pair_10 = convert_to_df(bat_BM48_pair_10)

bat_CDPHE15_pair_8 = convert_to_df(bat_CDPHE15_pair_8)
bat_CDPHE15_pair_9 = convert_to_df(bat_CDPHE15_pair_9)
bat_CDPHE15_pair_10 = convert_to_df(bat_CDPHE15_pair_10)

bat_1A_pair_8 = convert_to_df(bat_1A_pair_8)
bat_1A_pair_9 = convert_to_df(bat_1A_pair_9)
bat_1A_pair_10 = convert_to_df(bat_1A_pair_10)

tylonycteris_HKU4_pair_8 = convert_to_df(tylonycteris_HKU4_pair_8)
tylonycteris_HKU4_pair_9 = convert_to_df(tylonycteris_HKU4_pair_9)
tylonycteris_HKU4_pair_10 = convert_to_df(tylonycteris_HKU4_pair_10)

scotophilus_512_pair_8 = convert_to_df(scotophilus_512_pair_8)
scotophilus_512_pair_9 = convert_to_df(scotophilus_512_pair_9)
scotophilus_512_pair_10 = convert_to_df(scotophilus_512_pair_10)

pipistrellus_HKU5_pair_8 = convert_to_df(pipistrellus_HKU5_pair_8)
pipistrellus_HKU5_pair_9 = convert_to_df(pipistrellus_HKU5_pair_9)
pipistrellus_HKU5_pair_10 = convert_to_df(pipistrellus_HKU5_pair_10)

bat_NL63_pair_8 = convert_to_df(bat_NL63_pair_8)
bat_NL63_pair_9 = convert_to_df(bat_NL63_pair_9)
bat_NL63_pair_10 = convert_to_df(bat_NL63_pair_10)

bat_hp_pair_8 = convert_to_df(bat_hp_pair_8)
bat_hp_pair_9 = convert_to_df(bat_hp_pair_9)
bat_hp_pair_10 = convert_to_df(bat_hp_pair_10)

rhinolophus_HKU2_pair_8 = convert_to_df(rhinolophus_HKU2_pair_8)
rhinolophus_HKU2_pair_9 = convert_to_df(rhinolophus_HKU2_pair_9)
rhinolophus_HKU2_pair_10 = convert_to_df(rhinolophus_HKU2_pair_10)

miniopterus_HKU8_pair_8 = convert_to_df(miniopterus_HKU8_pair_8)
miniopterus_HKU8_pair_9 = convert_to_df(miniopterus_HKU8_pair_9)
miniopterus_HKU8_pair_10 = convert_to_df(miniopterus_HKU8_pair_10)

bat_coronavirus_pair_8 = convert_to_df(bat_coronavirus_pair_8)
bat_coronavirus_pair_9 = convert_to_df(bat_coronavirus_pair_9)
bat_coronavirus_pair_10 = convert_to_df(bat_coronavirus_pair_10)

munia_pair_8 = convert_to_df(munia_pair_8)
munia_pair_9 = convert_to_df(munia_pair_9)
munia_pair_10 = convert_to_df(munia_pair_10)

bovine_pair_8 = convert_to_df(bovine_pair_8)
bovine_pair_9 = convert_to_df(bovine_pair_9)
bovine_pair_10 = convert_to_df(bovine_pair_10)

rabbit_pair_8 = convert_to_df(rabbit_pair_8)
rabbit_pair_9 = convert_to_df(rabbit_pair_9)
rabbit_pair_10 = convert_to_df(rabbit_pair_10)

turkey_pair_8 = convert_to_df(turkey_pair_8)
turkey_pair_9 = convert_to_df(turkey_pair_9)
turkey_pair_10 = convert_to_df(turkey_pair_10)

porcine_epidemic_pair_8 = convert_to_df(porcine_epidemic_pair_8)
porcine_epidemic_pair_9 = convert_to_df(porcine_epidemic_pair_9)
porcine_epidemic_pair_10 = convert_to_df(porcine_epidemic_pair_10)

wencheng_pair_8 = convert_to_df(wencheng_pair_8)
wencheng_pair_9 = convert_to_df(wencheng_pair_9)
wencheng_pair_10 = convert_to_df(wencheng_pair_10)

betacoronavirus_erinaceus_pair_8 = convert_to_df(betacoronavirus_erinaceus_pair_8)
betacoronavirus_erinaceus_pair_9 = convert_to_df(betacoronavirus_erinaceus_pair_9)
betacoronavirus_erinaceus_pair_10 = convert_to_df(betacoronavirus_erinaceus_pair_10)

porcine_HKU15_pair_8 = convert_to_df(porcine_HKU15_pair_8)
porcine_HKU15_pair_9 = convert_to_df(porcine_HKU15_pair_9)
porcine_HKU15_pair_10 = convert_to_df(porcine_HKU15_pair_10)

rat_pair_8 = convert_to_df(rat_pair_8)
rat_pair_9 = convert_to_df(rat_pair_9)
rat_pair_10 = convert_to_df(rat_pair_10)

white_eye_pair_8 = convert_to_df(white_eye_pair_8)
white_eye_pair_9 = convert_to_df(white_eye_pair_9)
white_eye_pair_10 = convert_to_df(white_eye_pair_10)

thrush_pair_8 = convert_to_df(thrush_pair_8)
thrush_pair_9 = convert_to_df(thrush_pair_9)
thrush_pair_10 = convert_to_df(thrush_pair_10)

beluga_pair_8 = convert_to_df(beluga_pair_8)
beluga_pair_9 = convert_to_df(beluga_pair_9)
beluga_pair_10 = convert_to_df(beluga_pair_10)

camel_pair_8 = convert_to_df(camel_pair_8)
camel_pair_9 = convert_to_df(camel_pair_9)
camel_pair_10 = convert_to_df(camel_pair_10)

wigeon_pair_8 = convert_to_df(wigeon_pair_8)
wigeon_pair_9 = convert_to_df(wigeon_pair_9)
wigeon_pair_10 = convert_to_df(wigeon_pair_10)

lucheng_pair_8 = convert_to_df(lucheng_pair_8)
lucheng_pair_9 = convert_to_df(lucheng_pair_9)
lucheng_pair_10 = convert_to_df(lucheng_pair_10)

sparrow_pair_8 = convert_to_df(sparrow_pair_8)
sparrow_pair_9 = convert_to_df(sparrow_pair_9)
sparrow_pair_10 = convert_to_df(sparrow_pair_10)

bulbul_pair_8 = convert_to_df(bulbul_pair_8)
bulbul_pair_9 = convert_to_df(bulbul_pair_9)
bulbul_pair_10 = convert_to_df(bulbul_pair_10)

swine_pair_8 = convert_to_df(swine_pair_8)
swine_pair_9 = convert_to_df(swine_pair_9)
swine_pair_10 = convert_to_df(swine_pair_10)

magpie_pair_8 = convert_to_df(magpie_pair_8)
magpie_pair_9 = convert_to_df(magpie_pair_9)
magpie_pair_10 = convert_to_df(magpie_pair_10)

mink_pair_8 = convert_to_df(mink_pair_8)
mink_pair_9 = convert_to_df(mink_pair_9)
mink_pair_10 = convert_to_df(mink_pair_10)

bronchitis_pair_8 = convert_to_df(bronchitis_pair_8)
bronchitis_pair_9 = convert_to_df(bronchitis_pair_9)
bronchitis_pair_10 = convert_to_df(bronchitis_pair_10)

moorhen_pair_8 = convert_to_df(moorhen_pair_8)
moorhen_pair_9 = convert_to_df(moorhen_pair_9)
moorhen_pair_10 = convert_to_df(moorhen_pair_10)

betacoronavirus_HKU24_pair_8 = convert_to_df(betacoronavirus_HKU24_pair_8)
betacoronavirus_HKU24_pair_9 = convert_to_df(betacoronavirus_HKU24_pair_9)
betacoronavirus_HKU24_pair_10 = convert_to_df(betacoronavirus_HKU24_pair_10)

ferret_pair_8 = convert_to_df(ferret_pair_8)
ferret_pair_9 = convert_to_df(ferret_pair_9)
ferret_pair_10 = convert_to_df(ferret_pair_10)

betacoronavirus_england_pair_8 = convert_to_df(betacoronavirus_england_pair_8)
betacoronavirus_england_pair_9 = convert_to_df(betacoronavirus_england_pair_9)
betacoronavirus_england_pair_10 = convert_to_df(betacoronavirus_england_pair_10)

heron_pair_8 = convert_to_df(heron_pair_8)
heron_pair_9 = convert_to_df(heron_pair_9)
heron_pair_10 = convert_to_df(heron_pair_10)

In [90]:
SARS = pd.concat([sars_pair_8, sars_pair_9, sars_pair_10]).reset_index(drop=True)
MERS = pd.concat([mers_pair_8, mers_pair_9, mers_pair_9]).reset_index(drop=True)
SARS_COV_2 = pd.concat([sars_2_pair_8, sars_2_pair_9, sars_2_pair_10]).reset_index(drop=True)
HCOV_229E = pd.concat([hcov_229E_pair_8, hcov_229E_pair_9, hcov_229E_pair_10]).reset_index(drop=True)
HCOV_NL63 = pd.concat([hcov_NL63_pair_8, hcov_NL63_pair_9, hcov_NL63_pair_10]).reset_index(drop=True)
HCOV_HKU1 = pd.concat([hcov_HKU1_pair_8, hcov_HKU1_pair_9, hcov_HKU1_pair_10]).reset_index(drop=True)
HCOV_OC43 = pd.concat([hcov_OC43_pair_8, hcov_OC43_pair_9, hcov_OC43_pair_10]).reset_index(drop=True)

rousettus_bat = pd.concat([rousettus_bat_pair_8, rousettus_bat_pair_9, rousettus_bat_pair_10]).reset_index(drop=True)
rousettus_bat_HKU9 = pd.concat([rousettus_bat_HKU9_pair_8, rousettus_bat_HKU9_pair_9, rousettus_bat_HKU9_pair_10]).reset_index(drop=True)
rousettus_bat_HKU10 = pd.concat([rousettus_bat_HKU10_pair_8, rousettus_bat_HKU10_pair_9, rousettus_bat_HKU10_pair_10]).reset_index(drop=True)
bat_BM48 = pd.concat([bat_BM48_pair_8, bat_BM48_pair_9, bat_BM48_pair_10]).reset_index(drop=True)
bat_CDPHE15 = pd.concat([bat_CDPHE15_pair_8, bat_CDPHE15_pair_9, bat_CDPHE15_pair_10]).reset_index(drop=True)
bat_1A = pd.concat([bat_1A_pair_8, bat_1A_pair_9, bat_1A_pair_10]).reset_index(drop=True)
tylonycteris_HKU4 = pd.concat([tylonycteris_HKU4_pair_8, tylonycteris_HKU4_pair_9, tylonycteris_HKU4_pair_10]).reset_index(drop=True)
scotophilus_512 = pd.concat([scotophilus_512_pair_8, scotophilus_512_pair_9, scotophilus_512_pair_10]).reset_index(drop=True)
pipistrellus_HKU5 = pd.concat([pipistrellus_HKU5_pair_8, pipistrellus_HKU5_pair_9, pipistrellus_HKU5_pair_10]).reset_index(drop=True)
bat_NL63 = pd.concat([bat_NL63_pair_8, bat_NL63_pair_9, bat_NL63_pair_10]).reset_index(drop=True)
bat_hp = pd.concat([bat_hp_pair_8, bat_hp_pair_9, bat_hp_pair_10]).reset_index(drop=True)
rhinolophus_HKU2 = pd.concat([rhinolophus_HKU2_pair_8, rhinolophus_HKU2_pair_9, rhinolophus_HKU2_pair_10]).reset_index(drop=True)
miniopterus_HKU8 = pd.concat([miniopterus_HKU8_pair_8, miniopterus_HKU8_pair_9, miniopterus_HKU8_pair_10]).reset_index(drop=True)
bat_coronavirus = pd.concat([bat_coronavirus_pair_8, bat_coronavirus_pair_9, bat_coronavirus_pair_10]).reset_index(drop=True)

munia = pd.concat([munia_pair_8, munia_pair_9, munia_pair_10]).reset_index(drop=True)
bovine = pd.concat([bovine_pair_8, bovine_pair_9, bovine_pair_10]).reset_index(drop=True)
rabbit = pd.concat([rabbit_pair_8, rabbit_pair_9, rabbit_pair_10]).reset_index(drop=True)
turkey = pd.concat([turkey_pair_8, turkey_pair_9, turkey_pair_10]).reset_index(drop=True)
porcine_epidemic = pd.concat([porcine_epidemic_pair_8, porcine_epidemic_pair_9, porcine_epidemic_pair_10]).reset_index(drop=True)
wencheng = pd.concat([wencheng_pair_8, wencheng_pair_9, wencheng_pair_10]).reset_index(drop=True)
betacoronavirus_erinaceus = pd.concat([betacoronavirus_erinaceus_pair_8, betacoronavirus_erinaceus_pair_9, betacoronavirus_erinaceus_pair_10]).reset_index(drop=True)
porcine_HKU15 = pd.concat([porcine_HKU15_pair_8, porcine_HKU15_pair_9, porcine_HKU15_pair_10]).reset_index(drop=True)
rat = pd.concat([rat_pair_8, rat_pair_9, rat_pair_10]).reset_index(drop=True)
white_eye = pd.concat([white_eye_pair_8, white_eye_pair_9, white_eye_pair_10]).reset_index(drop=True)
thrush = pd.concat([thrush_pair_8, thrush_pair_9, thrush_pair_10]).reset_index(drop=True)
beluga = pd.concat([beluga_pair_8, beluga_pair_9, beluga_pair_10]).reset_index(drop=True)
camel = pd.concat([camel_pair_8, camel_pair_9, camel_pair_10]).reset_index(drop=True)
wigeon = pd.concat([wigeon_pair_8, wigeon_pair_9, wigeon_pair_10]).reset_index(drop=True)
lucheng = pd.concat([lucheng_pair_8, lucheng_pair_9, lucheng_pair_10]).reset_index(drop=True)
sparrow = pd.concat([sparrow_pair_8, sparrow_pair_9, sparrow_pair_10]).reset_index(drop=True)
bulbul = pd.concat([bulbul_pair_8, bulbul_pair_9, bulbul_pair_10]).reset_index(drop=True)
swine = pd.concat([swine_pair_8, swine_pair_9, swine_pair_10]).reset_index(drop=True)
magpie = pd.concat([magpie_pair_8, magpie_pair_9, magpie_pair_10]).reset_index(drop=True)
mink = pd.concat([mink_pair_8, mink_pair_9, mink_pair_10]).reset_index(drop=True)
bronchitis = pd.concat([bronchitis_pair_8, bronchitis_pair_9, bronchitis_pair_10]).reset_index(drop=True)
moorhen = pd.concat([moorhen_pair_8, moorhen_pair_9, moorhen_pair_10]).reset_index(drop=True)
betacoronavirus_HKU24 = pd.concat([betacoronavirus_HKU24_pair_8, betacoronavirus_HKU24_pair_9, betacoronavirus_HKU24_pair_10]).reset_index(drop=True)
ferret = pd.concat([ferret_pair_8, ferret_pair_9, ferret_pair_10]).reset_index(drop=True)
betacoronavirus_england = pd.concat([betacoronavirus_england_pair_8, betacoronavirus_england_pair_9, betacoronavirus_england_pair_10]).reset_index(drop=True)
heron = pd.concat([heron_pair_8, heron_pair_9, heron_pair_10]).reset_index(drop=True)

In [91]:
def explode(df, lst_cols, fill_value=''):
    # make sure `lst_cols` is a list
    if lst_cols and not isinstance(lst_cols, list):
        lst_cols = [lst_cols]
    # all columns except `lst_cols`
    idx_cols = df.columns.difference(lst_cols)

    # calculate lengths of lists
    lens = df[lst_cols[0]].str.len()

    if (lens > 0).all():
        # ALL lists in cells aren't empty
        return pd.DataFrame({
            col:np.repeat(df[col].values, df[lst_cols[0]].str.len())
            for col in idx_cols
        }).assign(**{col:np.concatenate(df[col].values) for col in lst_cols}) \
          .loc[:, df.columns]
    else:
        # at least one list in cells is empty
        return pd.DataFrame({
            col:np.repeat(df[col].values, df[lst_cols[0]].str.len())
            for col in idx_cols
        }).assign(**{col:np.concatenate(df[col].values) for col in lst_cols}) \
          .append(df.loc[lens==0, idx_cols]).fillna(fill_value) \
          .loc[:, df.columns]

In [92]:
def unstack_df(df):
    x = explode(df, lst_cols=["uniprot_annotation", "uniprot_gene"])
    x = explode(x, lst_cols=["viral_annotation", "viral_gene"])
    return x

In [93]:
SARS_unstacked = unstack_df(SARS)
MERS_unstacked = unstack_df(MERS)
SARS_COV_2_unstacked = unstack_df(SARS_COV_2)
HCOV_229E_unstacked = unstack_df(HCOV_229E)
HCOV_HKU1_unstacked = unstack_df(HCOV_HKU1)
HCOV_NL63_unstacked = unstack_df(HCOV_NL63)
HCOV_OC43_unstacked = unstack_df(HCOV_OC43)

rousettus_bat_unstacked = unstack_df(rousettus_bat)
rousettus_bat_HKU9_unstacked = unstack_df(rousettus_bat_HKU9)
rousettus_bat_HKU10_unstacked = unstack_df(rousettus_bat_HKU10)
bat_BM48_unstacked = unstack_df(bat_BM48)
bat_CDPHE15_unstacked = unstack_df(bat_CDPHE15)
bat_1A_unstacked = unstack_df(bat_1A)
tylonycteris_HKU4_unstacked = unstack_df(tylonycteris_HKU4)
scotophilus_512_unstacked = unstack_df(scotophilus_512)
pipistrellus_HKU5_unstacked = unstack_df(pipistrellus_HKU5)
bat_NL63_unstacked = unstack_df(bat_NL63)
bat_hp_unstacked = unstack_df(bat_hp)
rhinolophus_HKU2_unstacked = unstack_df(rhinolophus_HKU2)
miniopterus_HKU8_unstacked = unstack_df(miniopterus_HKU8)
bat_coronavirus_unstacked = unstack_df(bat_coronavirus)

munia_unstacked = unstack_df(munia)
bovine_unstacked = unstack_df(bovine)
rabbit_unstacked = unstack_df(rabbit)
turkey_unstacked = unstack_df(turkey)
porcine_epidemic_unstacked = unstack_df(porcine_epidemic)
wencheng_unstacked = unstack_df(wencheng)
betacoronavirus_erinaceus_unstacked = unstack_df(betacoronavirus_erinaceus)
porcine_HKU15_unstacked = unstack_df(porcine_HKU15)
rat_unstacked = unstack_df(rat)
white_eye_unstacked = unstack_df(white_eye)
thrush_unstacked = unstack_df(thrush)
beluga_unstacked = unstack_df(beluga)
camel_unstacked = unstack_df(camel)
wigeon_unstacked = unstack_df(wigeon)
lucheng_unstacked = unstack_df(lucheng)
sparrow_unstacked = unstack_df(sparrow)
bulbul_unstacked = unstack_df(bulbul)
swine_unstacked = unstack_df(swine)
magpie_unstacked = unstack_df(magpie)
mink_unstacked = unstack_df(mink)
bronchitis_unstacked = unstack_df(bronchitis)
moorhen_unstacked = unstack_df(moorhen)
betacoronavirus_HKU24_unstacked = unstack_df(betacoronavirus_HKU24)
ferret_unstacked = unstack_df(ferret)
betacoronavirus_england_unstacked = unstack_df(betacoronavirus_england)
heron_unstacked = unstack_df(heron)

In [94]:
def define_indexes(df):
    records = df.to_dict("records")
    for item in records:
        item["uniprot_start_ix"] = uniprot_dict[item["uniprot_annotation"]].find(item["nmer"])
        item["uniprot_end_ix"] = item["uniprot_start_ix"] + len(item["nmer"]) - 1
        item["viral_start_ix"] = viral_seq_dict[item["viral_annotation"]].find(item["nmer"])
        item["viral_end_ix"] = item["viral_start_ix"] + len(item["nmer"]) - 1
    df = pd.DataFrame(records)
    return df

In [95]:
SARS_unstacked_ix = define_indexes(SARS_unstacked)
MERS_unstacked_ix = define_indexes(MERS_unstacked)
SARS_COV_2_unstacked_ix = define_indexes(SARS_COV_2_unstacked)
HCOV_229E_unstacked_ix = define_indexes(HCOV_229E_unstacked)
HCOV_HKU1_unstacked_ix = define_indexes(HCOV_HKU1_unstacked)
HCOV_NL63_unstacked_ix = define_indexes(HCOV_NL63_unstacked)
HCOV_OC43_unstacked_ix = define_indexes(HCOV_OC43_unstacked)


# SARS_unstacked = unstack_df(SARS)
# MERS_unstacked = unstack_df(MERS)
# SARS_COV_2_unstacked = unstack_df(SARS_COV_2)
# HCOV_unstacked = unstack_df(HCOV)

rousettus_bat_unstacked_ix = define_indexes(rousettus_bat_unstacked)
rousettus_bat_HKU9_unstacked_ix = define_indexes(rousettus_bat_HKU9_unstacked)
rousettus_bat_HKU10_unstacked_ix = define_indexes(rousettus_bat_HKU10_unstacked)
bat_BM48_unstacked_ix = define_indexes(bat_BM48_unstacked)
bat_CDPHE15_unstacked_ix = define_indexes(bat_CDPHE15_unstacked)
bat_1A_unstacked_ix = define_indexes(bat_1A_unstacked)
tylonycteris_HKU4_unstacked_ix = define_indexes(tylonycteris_HKU4_unstacked)
scotophilus_512_unstacked_ix = define_indexes(scotophilus_512_unstacked)
pipistrellus_HKU5_unstacked_ix = define_indexes(pipistrellus_HKU5_unstacked)
bat_NL63_unstacked_ix = define_indexes(bat_NL63_unstacked)
bat_hp_unstacked_ix = define_indexes(bat_hp_unstacked)
rhinolophus_HKU2_unstacked_ix = define_indexes(rhinolophus_HKU2_unstacked)
miniopterus_HKU8_unstacked_ix = define_indexes(miniopterus_HKU8_unstacked)
bat_coronavirus_unstacked_ix = define_indexes(bat_coronavirus_unstacked)

munia_unstacked_ix = define_indexes(munia_unstacked)
bovine_unstacked_ix = define_indexes(bovine_unstacked)
rabbit_unstacked_ix = define_indexes(rabbit_unstacked)
turkey_unstacked_ix = define_indexes(turkey_unstacked)
porcine_epidemic_unstacked_ix = define_indexes(porcine_epidemic_unstacked)
wencheng_unstacked_ix = define_indexes(wencheng_unstacked)
betacoronavirus_erinaceus_unstacked_ix = define_indexes(betacoronavirus_erinaceus_unstacked)
porcine_HKU15_unstacked_ix = define_indexes(porcine_HKU15_unstacked)
rat_unstacked_ix = define_indexes(rat_unstacked)
white_eye_unstacked_ix = define_indexes(white_eye_unstacked)
thrush_unstacked_ix = define_indexes(thrush_unstacked)
beluga_unstacked_ix = define_indexes(beluga_unstacked)
camel_unstacked_ix = define_indexes(camel_unstacked)
wigeon_unstacked_ix = define_indexes(wigeon_unstacked)
lucheng_unstacked_ix = define_indexes(lucheng_unstacked)
sparrow_unstacked_ix = define_indexes(sparrow_unstacked)
bulbul_unstacked_ix = define_indexes(bulbul_unstacked)
swine_unstacked_ix = define_indexes(swine_unstacked)
magpie_unstacked_ix = define_indexes(magpie_unstacked)
mink_unstacked_ix = define_indexes(mink_unstacked)
bronchitis_unstacked_ix = define_indexes(bronchitis_unstacked)
moorhen_unstacked_ix = define_indexes(moorhen_unstacked)
betacoronavirus_HKU24_unstacked_ix = define_indexes(betacoronavirus_HKU24_unstacked)
ferret_unstacked_ix = define_indexes(ferret_unstacked)
betacoronavirus_england_unstacked_ix = define_indexes(betacoronavirus_england_unstacked)
heron_unstacked_ix = define_indexes(heron_unstacked)

In [96]:
def tranform_df(df):
    df = df.rename(columns={"uniprot_start_ix": "human_protein_peptide_start", "uniprot_end_ix": "human_protein_peptide_end", 
                            "viral_start_ix": "viral_protein_peptide_start", "viral_end_ix": "viral_protein_peptide_end", 
                            "nmer": "peptide", "length": "peptide_length", "uniprot_annotation": "human_protein_annotation", 
                            "viral_annotation": "viral_protein_annotation", "uniprot_gene": "human_protein"})
    df = pd.concat([df.drop("viral_gene", axis=1), pd.DataFrame(df.viral_gene.str.split('[', 1).tolist(), columns = ['viral_protein', 'viral_species'])], axis=1)
    df["viral_species"] = df["viral_species"].apply(lambda x: x.strip("]"))
    df["human_surprise_score"] = ""
    df["viral_surprise_score"] = ""
    df = df[["peptide", "peptide_length", "human_surprise_score", 
             "human_protein", "human_protein_annotation", "viral_surprise_score",
             "viral_species", "viral_protein", "viral_protein_annotation", 
             "human_protein_peptide_start", "human_protein_peptide_end", 
             "viral_protein_peptide_start", "viral_protein_peptide_end"]]
    return df

In [97]:
SARS_transformed = tranform_df(SARS_unstacked_ix)
MERS_transformed = tranform_df(MERS_unstacked_ix)
SARS_COV_2_transformed = tranform_df(SARS_COV_2_unstacked_ix)
HCOV_229E_transformed = tranform_df(HCOV_229E_unstacked_ix)
HCOV_HKU1_transformed = tranform_df(HCOV_HKU1_unstacked_ix)
HCOV_NL63_transformed = tranform_df(HCOV_NL63_unstacked_ix)
HCOV_OC43_transformed = tranform_df(HCOV_OC43_unstacked_ix)

rousettus_bat_transformed = tranform_df(rousettus_bat_unstacked_ix)
rousettus_bat_HKU9_transformed = tranform_df(rousettus_bat_HKU9_unstacked_ix)
rousettus_bat_HKU10_transformed = tranform_df(rousettus_bat_HKU10_unstacked_ix)
bat_BM48_transformed = tranform_df(bat_BM48_unstacked_ix)
bat_CDPHE15_transformed = tranform_df(bat_CDPHE15_unstacked_ix)
bat_1A_transformed = tranform_df(bat_1A_unstacked_ix)
tylonycteris_HKU4_transformed = tranform_df(tylonycteris_HKU4_unstacked_ix)
scotophilus_512_transformed = tranform_df(scotophilus_512_unstacked_ix)
pipistrellus_HKU5_transformed = tranform_df(pipistrellus_HKU5_unstacked_ix)
bat_NL63_transformed = tranform_df(bat_NL63_unstacked_ix)
bat_hp_transformed = tranform_df(bat_hp_unstacked_ix)
rhinolophus_HKU2_transformed = tranform_df(rhinolophus_HKU2_unstacked_ix)
miniopterus_HKU8_transformed = tranform_df(miniopterus_HKU8_unstacked_ix)
bat_coronavirus_transformed = tranform_df(bat_coronavirus_unstacked_ix)

munia_transformed = tranform_df(munia_unstacked_ix)
bovine_transformed = tranform_df(bovine_unstacked_ix)
rabbit_transformed = tranform_df(rabbit_unstacked_ix)
turkey_transformed = tranform_df(turkey_unstacked_ix)
porcine_epidemic_transformed = tranform_df(porcine_epidemic_unstacked_ix)
wencheng_transformed = tranform_df(wencheng_unstacked_ix)
betacoronavirus_erinaceus_transformed = tranform_df(betacoronavirus_erinaceus_unstacked_ix)
porcine_HKU15_transformed = tranform_df(porcine_HKU15_unstacked_ix)
rat_transformed = tranform_df(rat_unstacked_ix)
white_eye_transformed = tranform_df(white_eye_unstacked_ix)
thrush_transformed = tranform_df(thrush_unstacked_ix)
beluga_transformed = tranform_df(beluga_unstacked_ix)
camel_transformed = tranform_df(camel_unstacked_ix)
wigeon_transformed = tranform_df(wigeon_unstacked_ix)
lucheng_transformed = tranform_df(lucheng_unstacked_ix)
sparrow_transformed = tranform_df(sparrow_unstacked_ix)
bulbul_transformed = tranform_df(bulbul_unstacked_ix)
swine_transformed = tranform_df(swine_unstacked_ix)
magpie_transformed = tranform_df(magpie_unstacked_ix)
mink_transformed = tranform_df(mink_unstacked_ix)
bronchitis_transformed = tranform_df(bronchitis_unstacked_ix)
moorhen_transformed = tranform_df(moorhen_unstacked_ix)
betacoronavirus_HKU24_transformed = tranform_df(betacoronavirus_HKU24_unstacked_ix)
ferret_transformed = tranform_df(ferret_unstacked_ix)
betacoronavirus_england_transformed = tranform_df(betacoronavirus_england_unstacked_ix)
heron_transformed = tranform_df(heron_unstacked_ix)

In [175]:
type_dict = {"SARS-CoV-2": SARS_COV_2_transformed, "SARS": SARS_transformed, 
             "MERS": MERS_transformed, "H-CoV-22E": HCOV_229E_transformed, "H-CoV-OC43": HCOV_OC43_transformed,
             "H-CoV-NL63": HCOV_NL63_transformed, "H-CoV-HKU1": HCOV_HKU1_transformed,
             "rousettus_bat": rousettus_bat_transformed, 
             "rousettus_bat_HKU9": rousettus_bat_HKU9_transformed, "rousettus_bat_HKU10": rousettus_bat_HKU10_transformed, 
             "bat_BM48": bat_BM48_transformed, "bat_CDPHE15": bat_CDPHE15_transformed, "bat_1A": bat_1A_transformed, 
             "tylonycteris_HKU4": tylonycteris_HKU4_transformed, "scotophilus_512": scotophilus_512_transformed, 
             "pipistrellus_HKU5": pipistrellus_HKU5_transformed, "bat_NL63": bat_NL63_transformed, 
             "bat_hp": bat_hp_transformed, "rhinolophus_HKU2": rhinolophus_HKU2_transformed, 
             "miniopterus_HKU8": miniopterus_HKU8_transformed, "bat_coronavirus": bat_coronavirus_transformed, 
             "munia": munia_transformed, "bovine": bovine_transformed, "rabbit": rabbit_transformed, 
             "turkey": turkey_transformed, "porcine_epidemic": porcine_epidemic_transformed, 
             "wencheng": wencheng_transformed, "betacoronavirus_erinaceus": betacoronavirus_erinaceus_transformed, 
             "porcine_HKU15": porcine_HKU15_transformed, "rat": rat_transformed, "white_eye": white_eye_transformed, 
             "thrush": thrush_transformed, "beluga": beluga_transformed, "camel": camel_transformed, 
             "wigeon": wigeon_transformed, "lucheng": lucheng_transformed, "sparrow": sparrow_transformed, 
             "bulbul": bulbul_transformed, "swine": swine_transformed, "magpie": magpie_transformed, 
             "mink": mink_transformed, "bronchitis": bronchitis_transformed, "moorhen": moorhen_transformed, 
             "betacoronavirus_HKU24": betacoronavirus_HKU24_transformed, "ferret": ferret_transformed, 
             "betacoronavirus_england": betacoronavirus_england_transformed, "heron": heron_transformed
            }

In [99]:
save_xls(type_dict, "data/all_coronvirus_species_human_corona_split.xlsx")

In [176]:
dfs = []
for key, value in type_dict.items():
    value["key"] = key
    type_dict[key] = value
    dfs.append(value)
    type_dict[key] = value.to_dict("records")

In [177]:
main_mapper = pd.concat(dfs, join='outer', axis=0).to_dict("records")

In [178]:
for key, value in type_dict.items():
    for item in value:
        found_in = []
        for pep in main_mapper:
            if key != pep["key"]:
                if item["peptide"] == pep["peptide"]:
                    item[pep["key"]] = pep["viral_protein_annotation"] + " " + pep["viral_protein"]
    type_dict[key] = value

In [179]:
for key, value in type_dict.items():
    for item in value:
        del item["key"]

In [180]:
for key, value in type_dict.items():
    type_dict[key] = pd.DataFrame(value)

In [181]:
save_xls(type_dict, "data/all_coronvirus_species_pivot_columns_test_2.xlsx")

In [184]:
for key, value in type_dict.items():
    type_dict[key] = value.to_dict("records")

In [185]:
type_dict

{'SARS-CoV-2': [{'peptide': 'PGSGVPVV',
   'peptide_length': 8,
   'human_surprise_score': '',
   'human_protein': 'PAM',
   'human_protein_annotation': 'P19021',
   'viral_surprise_score': '',
   'viral_species': 'Severe acute respiratory syndrome coronavirus 2',
   'viral_protein': 'orf1ab polyprotein ',
   'viral_protein_annotation': 'YP_009724389.1',
   'human_protein_peptide_start': 859,
   'human_protein_peptide_end': 866,
   'viral_protein_peptide_start': 4618,
   'viral_protein_peptide_end': 4625,
   'SARS': nan,
   'pipistrellus_HKU5': nan,
   'MERS': nan,
   'H-CoV-OC43': nan,
   'H-CoV-HKU1': nan,
   'rousettus_bat': nan,
   'rousettus_bat_HKU9': nan,
   'bat_BM48': nan,
   'tylonycteris_HKU4': nan,
   'bat_hp': nan,
   'bat_coronavirus': nan,
   'bovine': nan,
   'rabbit': nan,
   'betacoronavirus_erinaceus': nan,
   'rat': nan,
   'betacoronavirus_HKU24': nan,
   'betacoronavirus_england': nan,
   'H-CoV-22E': nan,
   'H-CoV-NL63': nan,
   'rousettus_bat_HKU10': nan,
   'b

In [36]:
# pair_8 = pd.DataFrame.from_dict(data=pair_8, orient='index')
# pair_9 = pd.DataFrame.from_dict(data=pair_9, orient='index')
# pair_10 = pd.DataFrame.from_dict(data=pair_10, orient='index')
# pair_11 = pd.DataFrame.from_dict(data=pair_11, orient='index')
# pair_12 = pd.DataFrame.from_dict(data=pair_12, orient='index')

In [28]:
def save_xls(dict_df, path):
    writer = pd.ExcelWriter(path)
    for key in dict_df:
        dict_df[key].to_excel(writer, key)
    writer.save()

In [38]:
# nmer_dict = {"8mers": pair_8, "9mers": pair_9, "10mers": pair_10, "11mers": pair_11, "12mers": pair_12}

In [39]:
# save_xls(nmer_dict, "data/nmer_pairs_protein_map.xlsx")

In [35]:
viral_host = "/Users/nikhil/Downloads/viral.protein.host_count.txt"
ncbi_taxonomy = "/Users/nikhil/Downloads/taxonomy_NCBI-txid40674_mammalia.txt"

In [36]:
ncbi = list(csv.reader(open(ncbi_taxonomy, 'r'), delimiter='\t'))
viral_host_ = list(csv.reader(open(viral_host, 'r'), delimiter=' '))

In [37]:
ncbi_list = list(pd.DataFrame(ncbi)[0].values)
viral_host_filtered = [list(filter(None, lst)) for lst in viral_host_]

In [38]:
for viral_id in viral_host_filtered:
    if ast.literal_eval(viral_id[0]):
        viral_id = viral_id.pop(0)

In [40]:
viral_host_filtered = [" ".join(lst) for lst in viral_host_filtered]

In [47]:
present_in_both = list(set(viral_host_filtered) & set(ncbi_list))

In [75]:
len(present_in_both)

243

In [69]:
with open("overlap.json", "w") as fp:
    json.dump(present_in_both, fp)

In [83]:
l_ = []
for item in ncbi_list:
    for ids in viral_host_filtered:
        if ids in item:
            l_.append(item)

In [86]:
with open("subset_overlap_w_taxonomy.json", "w") as fp:
    json.dump(l_, fp)

In [85]:
len(l_)

1328